In [1]:
import pandas as pd
import numpy as np

#corpuse featurs (to combine for cossine similairity)
#genres, overview, production_companies, tagline, cast, crew, keywords
#quantitative: vote_average, rating, user rating average...

#be sure to check the column data t


pd.set_option('display.max_colwidth', None)

moviesFull = pd.read_csv('newdata/movies_metadata.csv',usecols=("genres","id" ,"title","tagline", "overview","production_companies"),
                          dtype={"tagline": "string", "id":"string", 'genres':"string", "title": "string", "tagline": "string","overview":"string", "production_companies" :"string"})
ratings = pd.read_csv('newdata/ratings.csv', usecols = ("userId", "movieId", "rating"), dtype={"userId": "string","movieId": "string","rating": "string"})
ratings = ratings.rename(columns={"movieId": "id"})

keywords = pd.read_csv('newdata/keywords.csv', usecols = ("id", "keywords"), dtype={"id": "string","keywords":"string"})
credits = pd.read_csv("newdata/credits.csv", usecols = ("cast", "id"), dtype={"cast": "string", "id": "string"})

complete =  pd.merge(moviesFull, ratings, on ="id")
complete =  pd.merge(complete,keywords, on ="id")
complete  = pd.merge(complete,credits, on ="id")


complete = complete.sort_values(by = 'userId')

complete  = complete.dropna()

complete  = complete.loc[:,['userId','id','rating',"title", "genres","production_companies","keywords", "cast", "tagline", "overview" ]]


print(complete)


        userId    id rating                       title  \
8830418      1  2959    4.0              License to Wed   
1690638      1  1968    4.0               Fools Rush In   
2343877      1  2762    4.5          Young and Innocent   
2943547      1   147    4.5               The 400 Blows   
8434697      1  1246    5.0                Rocky Balboa   
...        ...   ...    ...                         ...   
7550091  99998  1093    4.5     Elevator to the Gallows   
6020087  99999   780    3.0  The Passion of Joan of Arc   
845644   99999   260    5.0                The 39 Steps   
1272333  99999   235    4.0                 Stand by Me   
4685160  99999   161    4.0              Ocean's Eleven   

                                                                                                  genres  \
8830418                                                                   [{'id': 35, 'name': 'Comedy'}]   
1690638    [{'id': 18, 'name': 'Drama'}, {'id': 35, 'name': 'Comedy'}, {'id

In [14]:

import ast
#'userId','id','rating',"title", "genres","production_companies","keywords", "cast", "tagline", "overview"

def condition(array):
    length = len(array[4])
    if(array[4][length-2:] == "[]"):
        return False
    length = len(array[5])
    if(array[5][length-2:] == "[]"):
        return False
    length = len(array[6])
    if(array[6][length-2:] == "[]"):
        return False
    length = len(array[7])
    if(array[7][length-2:] == "[]"):
        return False   
    length = len(array[8])
    if(array[8][length-4:]=="<NA>"):
        return False
    length = len(array[9])
    if(array[9][length-4:]=="<NA>"):
        return False 
    return True

def populateNames(item):
    string  = item[1:-1]
    #list of to be jsons:
    jsons = string.split("}, ")
    
    names = ""
    cnt = 0
    for item in jsons:
        if(cnt == len(jsons)-1):
            tempDict = ast.literal_eval(item)
            names+=str(tempDict["name"])
        else:
            tempDict = ast.literal_eval(item+"}")
            names+=str(str(tempDict["name"])+" ")
        cnt += 1

    #print(names)
    return names


def provideData(array):
    movieData = []
    movieData.append(int(array[0]))
    movieData.append(int(array[1]))
    movieData.append(float(array[2]))
    movieData.append(array[3])  

    movieData.append(populateNames(array[4]))
    movieData.append(populateNames(array[5]))
    movieData.append(populateNames(array[6]))
    movieData.append(populateNames(array[7]))

    movieData.append(str(array[8]))
    movieData.append(str(array[9]))
    return movieData
    



#convert the data frame into a list then write it to a csv file

completeDict = dict()
completeArray = complete.to_numpy()
arrayOfUserIds = []

#print(completeArray)
#print(len(completeArray[0]))
#print(complete["tagline"])


lastId  = -1
for item in completeArray:
    if(item[0]!= lastId):
        arrayOfUserIds.append(item[0])
        lastId = item[0]


#print(arrayOfUserIds)
index  = 0

#remember to redefined data type
#not all the integers betwene 1 and 21 are user ids
#they have been used as indices instead

for i in range(0, 50):
    completeDict[arrayOfUserIds[i]] = []
    for j in range(index, len(completeArray)):
        if completeArray[j][0] == arrayOfUserIds[i]:
            #this is where conditions are checked for completeArray[j]
            if(condition(completeArray[j])):
                #this is where data is tranformed
                transformed = provideData(completeArray[j])
                completeDict[arrayOfUserIds[i]].append(transformed)         
        else:
            #ignore if the number o ratings is too small
            if (len(completeDict[arrayOfUserIds[i]])<10):
                del completeDict[arrayOfUserIds[i]]
            index = j+1
            break


for item in completeDict.keys():
    print(completeDict[item])


[[100000, 364, 5.0, 'Batman Returns', 'Action Fantasy', 'PolyGram Filmed Entertainment Warner Bros.', 'holiday corruption double life dc comics crime fighter hallucination christmas tree gotham city vigilante superhero violence dark hero fictional city super villain super powers deformed bird cage evil circus christmas holiday', 'Michael Keaton Danny DeVito Michelle Pfeiffer Christopher Walken Michael Gough Pat Hingle Vincent Schiavelli Michael Murphy Cristi Conaway Paul Reubens Diane Salinger', 'The Bat, the Cat, the Penguin.', "Having defeated the Joker, Batman now faces the Penguin - a warped and deformed individual who is intent on being accepted into Gotham society. Crooked businessman Max Schreck is coerced into helping him become Mayor of Gotham and they both attempt to expose Batman in a different light. Selina Kyle, Max's secretary, is thrown from the top of a building and is transformed into Catwoman - a mysterious figure who has the same personality disorder as Batman. Batma

In [15]:
#the above process takes 40 minutes so the date should besaved in a file
#this newly created file should be easily read
import csv


with open("constructedData/constructedData.csv", "w", encoding="utf-8", newline='') as f:
    writer = csv.writer(f)
    writer.writerow(['userId','id','rating',"title", "genres","production_companies","keywords", "cast", "tagline", "overview"])
    for item in completeDict.keys():
        writer.writerows(completeDict[item])


In [16]:
import csv

dataList =[]

with open("constructedData/constructedData.csv", 'r', encoding="utf-8") as read_obj:
    csv_reader = csv.reader(read_obj)
    dataList = list(csv_reader)

dataList = dataList[1:]


In [17]:
#movie id to rating
movieDict = dict()

#user id to the rated movies by that user
userDict = dict()

userId = -1
for row in dataList:
    if (row[0]!=userId):
        userId = row[0]
        userDict[row[0]] = [row]
    else:
        userDict[row[0]].append(row)

    if(row[1] in movieDict.keys()):
        movieDict[row[1]].append(row[2])
    else:
        movieDict[row[1]] = [row[2]]



In [24]:
from gensim.parsing.preprocessing import remove_stopwords

#dictionary of user id to corpus does not include...
#ratings or movie id
combinedCorpus = dict()

#littered with contractions that are not being removed
#note: escape character in the output is displayed for ' but the \ is not in the actual string

i = 0
for key in userDict.keys():
    movieStrings = []
    for movieData in userDict[key]:
        movieString = ""
        #avoid the first two data points id and rating
        for index in range (3,len(movieData)):
            if(index!= len(movieData)-1):
                movieString+= movieData[index]+" "
            else:
                movieString+= movieData[index]
        cleaned = remove_stopwords(movieString)
        movieStrings.append(cleaned)
    combinedCorpus[key] = movieStrings


for key in combinedCorpus.keys():
    print(len(combinedCorpus[key]))
    print(combinedCorpus[key])





Batman Returns Action Fantasy PolyGram Filmed Entertainment Warner Bros. holiday corruption double life dc comics crime fighter hallucination christmas tree gotham city vigilante superhero violence dark hero fictional city super villain super powers deformed bird cage evil circus christmas holiday Michael Keaton Danny DeVito Michelle Pfeiffer Christopher Walken Michael Gough Pat Hingle Vincent Schiavelli Michael Murphy Cristi Conaway Paul Reubens Diane Salinger The Bat, the Cat, the Penguin. Having defeated the Joker, Batman now faces the Penguin - a warped and deformed individual who is intent on being accepted into Gotham society. Crooked businessman Max Schreck is coerced into helping him become Mayor of Gotham and they both attempt to expose Batman in a different light. Selina Kyle, Max's secretary, is thrown from the top of a building and is transformed into Catwoman - a mysterious figure who has the same personality disorder as Batman. Batman must attempt to clear his name, all t

In [22]:
import numpy as np
from numpy import var
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.metrics.pairwise import cosine_similarity
import random
from matplotlib import pyplot as plt
from scipy.stats import norm
import numpy as np
from scipy import stats
from scipy.stats import norm
from sklearn.linear_model import LinearRegression
from sklearn.metrics import r2_score
import statistics
import math
from sklearn.neural_network import MLPRegressor
from sklearn.model_selection import train_test_split
import random
import copy
from gensim.parsing.preprocessing import remove_stopwords
from scipy.stats import kurtosis
from scipy.stats import skew

#analysis 

random.seed(1)

#this is a user dict issue not a movieDict issue
def getAverageMovieRatings(movieId):
    ret =0 
    cnt = 0
    for item in movieDict[movieId]:
        ret+= float(item)
        cnt+=1
    return (ret/cnt)


def getUserRatings(userId):
    ret = []
    for item in userDict[userId]:
        ret.append(float(item[2]))
    return ret


X = []
y = []


for key in combinedCorpus.keys():

    count_matrix = CountVectorizer().fit_transform(combinedCorpus[key]).toarray().tolist()
    randIndex = random.randint(0, len(count_matrix)-1)
    randTestItem = count_matrix[randIndex]
    del count_matrix[randIndex]

    cosine_sim = cosine_similarity(X = count_matrix ,Y = [randTestItem])

    ratings = copy.deepcopy(getUserRatings(key))
    randomRating = ratings[randIndex]
    del ratings[randIndex]


    similairities = np.reshape(cosine_sim,  (len(cosine_sim)))
    averageRating =  sum(ratings)/(len(ratings))

    features = []

    features.append(getAverageMovieRatings(userDict[key][randIndex][1]))
    features.append(averageRating)
    features.append(sum(similairities)/(len(similairities)))
    features.append(statistics.variance(ratings))
    features.append(statistics.variance(similairities))

    skew1= skew(ratings)
    skew2 = skew(similairities)
    kurt1 = kurtosis(ratings)
    kurt2 = kurtosis(similairities)


    lst = []
    for item in [skew1,skew2, kurt1, kurt2]:
        if(math.isnan(item)):
            lst.append(0)
        else:   
            lst.append(item)

    features.append(lst[0])
    features.append(lst[1])
    features.append(lst[2])
    features.append(lst[3])

    totalRating = 0

    for sim, rating in zip(similairities, ratings):
        totalRating += sim*(rating-averageRating)
    

    features.append(totalRating)
    X.append(features)
    y.append(randomRating)

print(X)
print(y)


[[2.5833333333333335, 4.388888888888889, 0.09193287020317208, 0.6045751633986928, 0.0013434782882646833, -0.778930086110198, 0.19740750067912474, -0.8406135865595301, -1.2038096041796964, -0.09462510163490764], [3.5, 4.015151515151516, 0.06395393239792632, 0.7575757575757576, 0.001050744742954317, -1.9600889489056559, 0.41773021511282044, 6.1104457031250075, -0.8442157718479404, -0.02032209917887034], [4.0, 3.6153846153846154, 0.053588577494950086, 0.9230769230769231, 0.0010838680946303105, -0.34027777777777807, 0.7304006342441061, -0.7187499999999982, -0.7301765188214615, -0.023648553051873796], [3.25, 3.822429906542056, 0.05295522960273755, 0.8077940398518779, 0.0007684060263438698, -0.6630318831655532, 0.5464534495506467, 0.1613450076459717, 0.16277768781054247, 0.04995209982909915], [4.0, 3.9411764705882355, 0.07142205728777806, 0.9891067538126361, 0.00229111915161751, -0.8344605140949256, 2.803886849636835, 0.27410817209726535, 12.988410665733776, 0.09344389395066696], [3.0, 3.722

In [23]:
from sklearn.model_selection import train_test_split

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=.25, random_state=1)
print(X)
print(y)

regr = MLPRegressor(hidden_layer_sizes=(100, 100,100),  max_iter=1000, random_state =1).fit(X_train, y_train)

score  = regr.score(X_test, y_test)
file = open("testing.txt", "a")
file.write("hidden_layer_sizes="+str(regr.hidden_layer_sizes)+", max_iter = "+str(regr.max_iter)+" " + str(score)+"\n")
file.close()

print("after nearal net regression:", score)
print(regr.max_iter)
print(regr.n_iter_)
print(regr.hidden_layer_sizes)

predicted = regr.predict(X_test)
for item, actual in zip(predicted, y_test):
    print("predicted:", item)
    print("actual:", actual)

[[2.5833333333333335, 4.388888888888889, 0.09193287020317208, 0.6045751633986928, 0.0013434782882646833, -0.778930086110198, 0.19740750067912474, -0.8406135865595301, -1.2038096041796964, -0.09462510163490764], [3.5, 4.015151515151516, 0.06395393239792632, 0.7575757575757576, 0.001050744742954317, -1.9600889489056559, 0.41773021511282044, 6.1104457031250075, -0.8442157718479404, -0.02032209917887034], [4.0, 3.6153846153846154, 0.053588577494950086, 0.9230769230769231, 0.0010838680946303105, -0.34027777777777807, 0.7304006342441061, -0.7187499999999982, -0.7301765188214615, -0.023648553051873796], [3.25, 3.822429906542056, 0.05295522960273755, 0.8077940398518779, 0.0007684060263438698, -0.6630318831655532, 0.5464534495506467, 0.1613450076459717, 0.16277768781054247, 0.04995209982909915], [4.0, 3.9411764705882355, 0.07142205728777806, 0.9891067538126361, 0.00229111915161751, -0.8344605140949256, 2.803886849636835, 0.27410817209726535, 12.988410665733776, 0.09344389395066696], [3.0, 3.722